Import neccesary libraries

In [10]:
!pip install pulp
import numpy as np
import pandas as pd
from pulp import *
import math
from scipy.sparse import csr_matrix

Defaulting to user installation because normal site-packages is not writeable


Call town names and their production (Weighted production)

In [11]:
# Load data from CSV
data = pd.read_excel('LocationForecastAll.xlsx')
print(data)

                City  Weighted Production  ...  Unnamed: 52  Unnamed: 53
0         Abaetetuba             0.236718  ...          NaN          NaN
1    Abel Figueiredo             0.000000  ...          NaN          NaN
2        Abreulândia             0.000000  ...          NaN          NaN
3         Açailândia             0.000000  ...          NaN          NaN
4              Acará             1.495490  ...          NaN          NaN
..               ...                  ...  ...          ...          ...
762     Wanderlândia             0.000000  ...          NaN          NaN
763          Xambioá             0.000000  ...          NaN          NaN
764           Xapuri             1.340790  ...          NaN          NaN
765         Xinguara             0.002310  ...          NaN          NaN
766          Zé Doca             0.000000  ...          NaN          NaN

[767 rows x 54 columns]


Create list of town name and it's weighted production per year

In [12]:
Name = data['City'].to_numpy()
custm_demands = data['Weighted Production'].to_numpy()
print(Name)
print(custm_demands)

['Abaetetuba' 'Abel Figueiredo' 'Abreulândia' 'Açailândia' 'Acará'
 'Acorizal' 'Acrelândia' 'Afuá' 'Água Azul do Norte' 'Água Boa'
 'Aguiarnópolis' 'Alcântara' 'Alenquer' 'Aliança do Tocantins' 'Almas'
 'Almeirim' 'Alta Floresta' "Alta Floresta D'Oeste" 'Altamira'
 'Altamira do Maranhão' 'Alto Alegre' 'Alto Alegre do Maranhão'
 'Alto Alegre do Pindaré' 'Alto Alegre dos Parecis' 'Alto Araguaia'
 'Alto Boa Vista' 'Alto Garças' 'Alto Paraguai' 'Alto Paraíso'
 'Alto Parnaíba' 'Alto Taquari' 'Alvarães' 'Alvorada' "Alvorada D'Oeste"
 'Amajari' 'Amapá' 'Amapá do Maranhão' 'Amarante do Maranhão' 'Amaturá'
 'Anajás' 'Anajatuba' 'Anamã' 'Ananás' 'Ananindeua' 'Anapu' 'Angico'
 'Anori' 'Aparecida do Rio Negro' 'Apiacás' 'Apicum-Açu' 'Apuí'
 'Aragominas' 'Araguacema' 'Araguaçu' 'Araguaiana' 'Araguaína'
 'Araguainha' 'Araguanã' 'Araguatins' 'Arame' 'Arapoema' 'Araputanga'
 'Arari' 'Arenápolis' 'Aripuanã' 'Ariquemes' 'Arraias' 'Assis Brasil'
 'Atalaia do Norte' 'Augustinópolis' 'Augusto Corrêa' 'Auro

In [ ]:
Selecting the towns which could be used as a factory location candidates. Here 30 top producer per year is selected, parameters could be added for different number of candidates or based on their location,GDP,population.

In [13]:
# Define facility demands and coordinates based on demand threshold
facil_threshold = 1.65 # Minimum weigthed production per day required to have a factory
Fac_Name = data[data['Weighted Production'] > facil_threshold]['City'].to_numpy()
Factory = []
for i in range(len(Fac_Name)):
    loc = (np.where(Name == Fac_Name[i]))
    Factory.append(loc[0].item())
print("Town which can have factory")
print(Fac_Name)

Town which can have factory
['Afuá' 'Beruri' 'Boca do Acre' 'Brasiléia' 'Coari' 'Codajás' 'Humaitá'
 'Igarapé-Miri' 'Inhangapi' 'Itacoatiara' 'Lábrea' 'Limoeiro do Ajuru'
 'Luís Domingues' 'Magalhães Barata' 'Manicoré' 'Marapanim' 'Mocajuba'
 'Muaná' 'Nova Olinda do Maranhão' 'Novo Aripuanã' 'Óbidos'
 'Oeiras do Pará' 'Oriximiná' 'Ponta de Pedras' 'Porto Velho' 'Rio Branco'
 'São Domingos do Capim' 'São Miguel do Guamá'
 'São Sebastião da Boa Vista' 'Sena Madureira']


Defining mode parameters

In [14]:
Mode = ['Ferry with Freezer', 'Mid Size ferry', 'Refrigerator truck','Normal Truck']
mode_capacity = [125, 150, 18, 22.5]
mode_fcost = [600000, 2000000, 150000, 100000]
mode_vcost = [ 0.125, 0.0435, 3, 1.75]
mode_speed = [20, 21, 80, 80]

Load OD matrixes for river and road way based on the town and facility location candidates location 

In [17]:
# Load distance matrices (/1000 to be km)
dist_matrix_River = (pd.read_excel('RiverDistance.xlsx', usecols = Factory, header=None).values / 1000)
dist_matrix_Road = (pd.read_excel('RoadDistance.xlsx', usecols = Factory,header=None).values / 1000)
print("River OD")
print(dist_matrix_River)
print("Road OD")
print(dist_matrix_Road)

River OD
[[ 343.96199976 1876.21703888 3514.45456054 ...    0.
   389.54269673 3688.34809414]
 [ 912.94230952 2350.79399406 3989.03151571 ... 1139.3996145
   958.5230065  4162.92504932]
 [1936.54926372 2925.15604482 4563.39356647 ... 2163.0065687
  1982.1299607  4737.28710008]
 ...
 [3721.14039826 1959.32626843  328.4406543  ... 3947.59770324
  3766.72109523  520.81010959]
 [1554.52837843 2543.13515953 4181.37268118 ... 1780.98568341
  1600.10907541 4355.26621479]
 [ 722.92484223 2255.17988135 3893.41740301 ...    0.
   768.5055392  4067.31093661]]
Road OD
[[   0.            0.            0.         ...    0.
     0.            0.        ]
 [   0.         3716.6230888  3694.61821309 ...  506.23553317
   678.35852981    0.        ]
 [   0.         3139.53593402 3117.53105831 ... 1179.7558668
  1351.87886343    0.        ]
 ...
 [   0.            0.            0.         ...    0.
     0.            0.        ]
 [   0.         3203.66960141 3181.6647257  ... 1024.81931268
  1196.94230931

In [18]:
# Define decision variable
S = ['S' + str(i + 1) for i in range(len(Factory))]  # Factory
D = ['D' + str(i + 1) for i in range(767)]  # Town
M = ['M' + str(i + 1) for i in range(len(Mode))]  # Mode
print(S)
print(D)
print(M)

['S1', 'S2', 'S3', 'S4', 'S5', 'S6', 'S7', 'S8', 'S9', 'S10', 'S11', 'S12', 'S13', 'S14', 'S15', 'S16', 'S17', 'S18', 'S19', 'S20', 'S21', 'S22', 'S23', 'S24', 'S25', 'S26', 'S27', 'S28', 'S29', 'S30']
['D1', 'D2', 'D3', 'D4', 'D5', 'D6', 'D7', 'D8', 'D9', 'D10', 'D11', 'D12', 'D13', 'D14', 'D15', 'D16', 'D17', 'D18', 'D19', 'D20', 'D21', 'D22', 'D23', 'D24', 'D25', 'D26', 'D27', 'D28', 'D29', 'D30', 'D31', 'D32', 'D33', 'D34', 'D35', 'D36', 'D37', 'D38', 'D39', 'D40', 'D41', 'D42', 'D43', 'D44', 'D45', 'D46', 'D47', 'D48', 'D49', 'D50', 'D51', 'D52', 'D53', 'D54', 'D55', 'D56', 'D57', 'D58', 'D59', 'D60', 'D61', 'D62', 'D63', 'D64', 'D65', 'D66', 'D67', 'D68', 'D69', 'D70', 'D71', 'D72', 'D73', 'D74', 'D75', 'D76', 'D77', 'D78', 'D79', 'D80', 'D81', 'D82', 'D83', 'D84', 'D85', 'D86', 'D87', 'D88', 'D89', 'D90', 'D91', 'D92', 'D93', 'D94', 'D95', 'D96', 'D97', 'D98', 'D99', 'D100', 'D101', 'D102', 'D103', 'D104', 'D105', 'D106', 'D107', 'D108', 'D109', 'D110', 'D111', 'D112', 'D113', '

In [21]:
# Define parameters
# Facility Capacities
facil_capacities = 150  # 150 tonnes
capacity_unit_cost = 4627500  # $ per facility open
P = {facility: facil_capacities for facility in S}
# Facility Cost
c = {facility: capacity_unit_cost for facility in S}
# Customer demands
Q = {customer: custm_demands[i] for i, customer in enumerate(D)}
# Customer-Facility distance based on mode
d = {customer: {facility: {mode: (dist_matrix_River[i, j] if k < 2 else dist_matrix_Road[i, j])
            for k, mode in enumerate(M)
        }
        for j, facility in enumerate(S)
    }
    for i, customer in enumerate(D)
}
# Mode capacity
m = {mode: mode_capacity[k] for k, mode in enumerate(M)}
# Mode total Cost (Sum of fix cost(Customer demand * mode fix cost/mode capacity) and variable cost(distance for ij route using k mode * customer demand * mode variable cost))
mc = {customer: {facility: {mode: (
                math.ceil(Q[customer] / m[mode]) * mode_fcost[k] * (d[customer][facility][mode] if int(d[customer][facility][mode]) == 0 else 1) +
                (d[customer][facility][mode]) * mode_vcost[k] * Q[customer] * math.ceil(Q[customer] / m[mode]))
                for k, mode in enumerate(M)
        }
        for j, facility in enumerate(S)
    }
    for i, customer in enumerate(D)
}
# Mode Speed
s = {mode: mode_speed[k] for k, mode in enumerate(M)}
print("Example parameter distance between origin D to destination S using mode M")
print(d)

Example parameter distance between origin D to destination S using mode M
{'D1': {'S1': {'M1': 343.9619997568, 'M2': 343.9619997568, 'M3': 0.0, 'M4': 0.0}, 'S2': {'M1': 1876.2170388839, 'M2': 1876.2170388839, 'M3': 0.0, 'M4': 0.0}, 'S3': {'M1': 3514.4545605394997, 'M2': 3514.4545605394997, 'M3': 0.0, 'M4': 0.0}, 'S4': {'M1': 3902.4193890378, 'M2': 3902.4193890378, 'M3': 0.0, 'M4': 0.0}, 'S5': {'M1': 2075.7313230496, 'M2': 2075.7313230496, 'M3': 0.0, 'M4': 0.0}, 'S6': {'M1': 1933.2673771413, 'M2': 1933.2673771413, 'M3': 0.0, 'M4': 0.0}, 'S7': {'M1': 2323.7924157944, 'M2': 2323.7924157944, 'M3': 0.0, 'M4': 0.0}, 'S8': {'M1': 0.0, 'M2': 0.0, 'M3': 0.0, 'M4': 0.0}, 'S9': {'M1': 0.0, 'M2': 0.0, 'M3': 0.0, 'M4': 0.0}, 'S10': {'M1': 1441.2178631036, 'M2': 1441.2178631036, 'M3': 0.0, 'M4': 0.0}, 'S11': {'M1': 2946.1681150112, 'M2': 2946.1681150112, 'M3': 0.0, 'M4': 0.0}, 'S12': {'M1': 417.81589894480004, 'M2': 417.81589894480004, 'M3': 0.0, 'M4': 0.0}, 'S13': {'M1': 0.0, 'M2': 0.0, 'M3': 0.0, 

In [26]:
# Decision variables
x = LpVariable.dicts('x', (D, S, M), lowBound=0, cat=LpContinuous)  # Quantity on route D to S using M
y = LpVariable.dicts('y', S, lowBound=0, upBound=1, cat=LpInteger)  # Facility open or not
z = LpVariable.dicts('z', (D, S, M), lowBound=0, upBound=1, cat=LpInteger)  # Route.mode used open or not
print("Creating decision variables, example is x:Quantity on route D to S using mode M")
print(x)

Creating decision variables, example is x:Quantity on route D to S using mode M
{'D1': {'S1': {'M1': x_D1_S1_M1, 'M2': x_D1_S1_M2, 'M3': x_D1_S1_M3, 'M4': x_D1_S1_M4}, 'S2': {'M1': x_D1_S2_M1, 'M2': x_D1_S2_M2, 'M3': x_D1_S2_M3, 'M4': x_D1_S2_M4}, 'S3': {'M1': x_D1_S3_M1, 'M2': x_D1_S3_M2, 'M3': x_D1_S3_M3, 'M4': x_D1_S3_M4}, 'S4': {'M1': x_D1_S4_M1, 'M2': x_D1_S4_M2, 'M3': x_D1_S4_M3, 'M4': x_D1_S4_M4}, 'S5': {'M1': x_D1_S5_M1, 'M2': x_D1_S5_M2, 'M3': x_D1_S5_M3, 'M4': x_D1_S5_M4}, 'S6': {'M1': x_D1_S6_M1, 'M2': x_D1_S6_M2, 'M3': x_D1_S6_M3, 'M4': x_D1_S6_M4}, 'S7': {'M1': x_D1_S7_M1, 'M2': x_D1_S7_M2, 'M3': x_D1_S7_M3, 'M4': x_D1_S7_M4}, 'S8': {'M1': x_D1_S8_M1, 'M2': x_D1_S8_M2, 'M3': x_D1_S8_M3, 'M4': x_D1_S8_M4}, 'S9': {'M1': x_D1_S9_M1, 'M2': x_D1_S9_M2, 'M3': x_D1_S9_M3, 'M4': x_D1_S9_M4}, 'S10': {'M1': x_D1_S10_M1, 'M2': x_D1_S10_M2, 'M3': x_D1_S10_M3, 'M4': x_D1_S10_M4}, 'S11': {'M1': x_D1_S11_M1, 'M2': x_D1_S11_M2, 'M3': x_D1_S11_M3, 'M4': x_D1_S11_M4}, 'S12': {'M1': x_D1_S12

In [28]:
# Define Objective function options
#Minimise per trip (z) or per unit delivered (x)
def objective_function(option):
    if option == 1:  # Minimise cost for initial investment and 1 day operation
        return lpSum([mc[i][j][k] * x[i][j][k]
                    for i in D
                    for j in S
                    for k in M
                    ]) + lpSum([c[j] * y[j]
                    for j in S
                    ])
    elif option == 2:  # Minimise time
        return lpSum([(d[i][j][k] / s[k]) * x[i][j][k]
                    for i in D
                    for j in S
                    for k in M
                    ])
    elif option == 3:  # Minimise cost and time
        return lpSum([(mc[i][j][k]/10000) * x[i][j][k]
                    for i in D
                    for j in S
                    for k in M
                    ]) + lpSum([c[j] * y[j]
                    for j in S
                    ]) + lpSum([(d[i][j][k] / s[k]) * x[i][j][k]
                    for i in D
                    for j in S
                    for k in M
                    ])


# Set the objective function (option 1, 2, or 3)
objective_option = 1
prob = LpProblem('prob', LpMinimize)
prob += objective_function(objective_option)
print("Generate the desire objective function")
print(prob)

Generate the desire objective function
prob:
MINIMIZE
4627500*y_S1 + 4627500*y_S10 + 4627500*y_S11 + 4627500*y_S12 + 4627500*y_S13 + 4627500*y_S14 + 4627500*y_S15 + 4627500*y_S16 + 4627500*y_S17 + 4627500*y_S18 + 4627500*y_S19 + 4627500*y_S2 + 4627500*y_S20 + 4627500*y_S21 + 4627500*y_S22 + 4627500*y_S23 + 4627500*y_S24 + 4627500*y_S25 + 4627500*y_S26 + 4627500*y_S27 + 4627500*y_S28 + 4627500*y_S29 + 4627500*y_S3 + 4627500*y_S30 + 4627500*y_S4 + 4627500*y_S5 + 4627500*y_S6 + 4627500*y_S7 + 4627500*y_S8 + 4627500*y_S9 + 600008.9038898913*z_D101_S10_M1 + 2000003.0985536822*z_D101_S10_M2 + 600018.0489373743*z_D101_S11_M1 + 2000006.2810302062*z_D101_S11_M2 + 150556.00827148938*z_D101_S11_M3 + 100324.33815836882*z_D101_S11_M4 + 600002.6850401025*z_D101_S12_M1 + 2000000.9343939556*z_D101_S12_M2 + 150094.94149772986*z_D101_S12_M3 + 100055.38254034243*z_D101_S12_M4 + 150083.09950324532*z_D101_S13_M3 + 100048.47471022644*z_D101_S13_M4 + 150057.24910872712*z_D101_S14_M3 + 100033.39531342416*z_D1

In [30]:
# Define constraints
print("Generating the constraints, Example is the product must be delivered")
# Each customer's product must be delivered
for i in D:
    prob += lpSum([x[i][j][k] for j in S for k in M]) == Q[i]
    print(lpSum([x[i][j][k] for j in S for k in M]) == Q[i])
# Ensure that a facility is open if it is used
for i in D:
    for j in S:
        prob += lpSum([z[i][j][k] for k in M]) <= y[j]
        
# Prevent trip with zero distance
for i in D:
    for j in S:
        for k in M:
            if d[i][j][k] == 0 and i != j:
                prob += z[i][j][k] == 0
                
# Each facility's capacity must not be exceeded
for j in S:
    prob += lpSum([x[i][j][k] for i in D for k in M]) <= P[j] * y[j]
    
# At least n_min and at most n_max facilities should be used
n_min = 1
n_max = len(Factory)
prob += lpSum([y[j] for j in S]) >= n_min
prob += lpSum([y[j] for j in S]) <= n_max

# Only one mode is used for each customer-facility pair
for i in D:
    for j in S:
        prob += lpSum([z[i][j][k] for k in M]) <= 1
        
# Each customer is assigned to only one facility
for i in D: 
    prob += lpSum([z[i][j][k] for j in S for k in M]) == 1
    
# z and x relationship
for i in D:
    for j in S:
        for k in M:
            prob += x[i][j][k] <= Q[i] * z[i][j][k]
            prob += z[i][j][k] <= y[j]
            
# Travel time constraint: time must be less than 24 hours
for i in D:
    for j in S:
        for k in M:
            if k not in ['M1', 'M3']:
                prob += (d[i][j][k] / s[k]) * z[i][j][k] <= 24
                


Generating the constraints, Example is the product must be delivered
x_D1_S10_M1 + x_D1_S10_M2 + x_D1_S10_M3 + x_D1_S10_M4 + x_D1_S11_M1 + x_D1_S11_M2 + x_D1_S11_M3 + x_D1_S11_M4 + x_D1_S12_M1 + x_D1_S12_M2 + x_D1_S12_M3 + x_D1_S12_M4 + x_D1_S13_M1 + x_D1_S13_M2 + x_D1_S13_M3 + x_D1_S13_M4 + x_D1_S14_M1 + x_D1_S14_M2 + x_D1_S14_M3 + x_D1_S14_M4 + x_D1_S15_M1 + x_D1_S15_M2 + x_D1_S15_M3 + x_D1_S15_M4 + x_D1_S16_M1 + x_D1_S16_M2 + x_D1_S16_M3 + x_D1_S16_M4 + x_D1_S17_M1 + x_D1_S17_M2 + x_D1_S17_M3 + x_D1_S17_M4 + x_D1_S18_M1 + x_D1_S18_M2 + x_D1_S18_M3 + x_D1_S18_M4 + x_D1_S19_M1 + x_D1_S19_M2 + x_D1_S19_M3 + x_D1_S19_M4 + x_D1_S1_M1 + x_D1_S1_M2 + x_D1_S1_M3 + x_D1_S1_M4 + x_D1_S20_M1 + x_D1_S20_M2 + x_D1_S20_M3 + x_D1_S20_M4 + x_D1_S21_M1 + x_D1_S21_M2 + x_D1_S21_M3 + x_D1_S21_M4 + x_D1_S22_M1 + x_D1_S22_M2 + x_D1_S22_M3 + x_D1_S22_M4 + x_D1_S23_M1 + x_D1_S23_M2 + x_D1_S23_M3 + x_D1_S23_M4 + x_D1_S24_M1 + x_D1_S24_M2 + x_D1_S24_M3 + x_D1_S24_M4 + x_D1_S25_M1 + x_D1_S25_M2 + x_D1_S25_M3

In [31]:
# Solve the problem
status = prob.solve()

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /home/repl/.local/lib/python3.10/site-packages/pulp/solverdir/cbc/linux/64/cbc /tmp/c021bec42cca49d68c383598c782eb7f-pulp.mps -timeMode elapsed -branch -printingOptions all -solution /tmp/c021bec42cca49d68c383598c782eb7f-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 593821 COLUMNS
At line 2518792 RHS
At line 3112609 BOUNDS
At line 3204680 ENDATA
Problem MODEL has 593816 rows, 184110 columns and 1711462 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 7.79375e+07 - 60.47 seconds
Cgl0002I 19222 variables fixed
Cgl0003I 0 fixed, 0 tightened bounds, 4154 strengthened rows, 129 substitutions
Cgl0003I 0 fixed, 1 tightened bounds, 4251 strengthened rows, 0 substitutions
Cgl0003I 0 fixed, 697 tightened bounds, 3466 strengthened rows, 0 substitutions
Cgl0003I 0 fixed, 460 tightened bounds, 3764 str

In [33]:
# Output the results
totalcost = 0
totaltime = 0
chosen_facilities = []
for i in D:
    for j in S:
        for k in M:
            if x[i][j][k].varValue > 0:
                # Determine which distance matrix is used
                mode_index = int(k[1:]) - 1
                if mode_index < 2:
                    distance_matrix = "River"
                    distance = dist_matrix_River[int(i[1:]) - 1, int(j[1:]) - 1]
                else:
                    distance_matrix = "Road"
                    distance = dist_matrix_Road[int(i[1:]) - 1, int(j[1:]) - 1]

                # Calculate travel time based on the chosen mode
                travel_time = distance / s[k]
                num_vehicles = math.ceil(x[i][j][k].varValue / m[k])
                route_cost = mc[i][j][k]
                totalcost += route_cost
                totaltime += travel_time * num_vehicles  # Sum travel time for all vehicles
                print(travel_time)
                print(f"Customer {i} ({Name[int(i[1:]) - 1]}) to Facility {j} ({Fac_Name[int(j[1:]) - 1]}) using {Mode[mode_index]}")
                print(f"  Quantity: {x[i][j][k].varValue}")
                print(f"  Number of vehicles: {num_vehicles}")
                print(f"  Travel time: {travel_time} hours per vehicle")
                print(f"  Total travel time for all vehicles: {travel_time * num_vehicles} hours")
                print(f"  Cost for this route: {route_cost}")
                print(f"  Distance matrix used: {distance_matrix}")
                print(f"  Distance: {distance} km")




184.41740470717
Customer D1 (Abaetetuba) to Facility S30 (Sena Madureira) using Ferry with Freezer
  Quantity: 0.23671837
  Number of vehicles: 1
  Travel time: 184.41740470717 hours per vehicle
  Total travel time for all vehicles: 184.41740470717 hours
  Cost for this route: 600109.1374672217
  Distance matrix used: River
  Distance: 3688.3480941434 km
1.57548258975
Customer D5 (Acará) to Facility S28 (São Miguel do Guamá) using Normal Truck
  Quantity: 1.4954904
  Number of vehicles: 1
  Travel time: 1.57548258975 hours per vehicle
  Total travel time for all vehicles: 1.57548258975 hours
  Cost for this route: 100329.85667148509
  Distance matrix used: Road
  Distance: 126.03860718 km
1.44696887655625
Customer D7 (Acrelândia) to Facility S26 (Rio Branco) using Normal Truck
  Quantity: 0.87092343
  Number of vehicles: 1
  Travel time: 1.44696887655625 hours per vehicle
  Total travel time for all vehicles: 1.44696887655625 hours
  Cost for this route: 100176.42787379288
  Distance m

In [34]:
for j in S:
    if y[j].varValue > 0:
        chosen_facilities.append(Fac_Name[int(j[1:]) - 1])
        print(f"\nFacility {j} ({Fac_Name[int(j[1:]) - 1]}) used")

FacCount = len(chosen_facilities)
FacCost = FacCount * capacity_unit_cost
NetworkTotalCost = FacCost + totalcost
print(f"Chosen facilities: {chosen_facilities}")
print(f"Network total transportation cost: {totalcost}")
print(f"Network total cost: {NetworkTotalCost}")
print(f"Network total time: {totaltime} hours")
print(f'STATUS\n{LpStatus[status]}\n')


Facility S26 (Rio Branco) used

Facility S28 (São Miguel do Guamá) used

Facility S30 (Sena Madureira) used
Chosen facilities: ['Rio Branco', 'São Miguel do Guamá', 'Sena Madureira']
Network total transportation cost: 70464700.0872243
Network total cost: 84347200.0872243
Network total time: 9567.214337039559 hours
STATUS
Optimal



In [35]:
# Initialize lists to store data
results_data = []
facility_data = []

# Iterate over the decision variables to collect results
for i in D:
    for j in S:
        for k in M:
            if x[i][j][k].varValue > 0:
                mode_index = int(k[1:]) - 1
                if mode_index < 2:
                    distance_matrix = "River"
                    distance = dist_matrix_River[int(i[1:]) - 1, int(j[1:]) - 1]
                else:
                    distance_matrix = "Road"
                    distance = dist_matrix_Road[int(i[1:]) - 1, int(j[1:]) - 1]

                travel_time = distance / s[k]
                num_vehicles = math.ceil(x[i][j][k].varValue / m[k])
                route_cost = mc[i][j][k]   
                results_data.append([
                    Name[int(i[1:]) - 1],
                    Fac_Name[int(j[1:]) - 1],
                    Mode[mode_index],
                    x[i][j][k].varValue,
                    num_vehicles,
                    travel_time,
                    travel_time * num_vehicles,
                    route_cost,
                    distance_matrix,
                    distance
                ])
# Append chosen facilities data
for j in S:
    if y[j].varValue > 0:
        facility_data.append(Fac_Name[int(j[1:]) - 1])

# Convert lists to DataFrame
results_df = pd.DataFrame(results_data, columns=[
    'Origin', 'Destination', 'Mode', 'Quantity', 'Number of Vehicles', 
    'Travel Time (hrs/vehicle)', 'Total Travel Time (hrs)', 
    'Cost for this Route', 'Distance Matrix Used', 'Distance (km)' 
])
network_data = [[
    NetworkTotalCost,
    totaltime
]]


facility_df = pd.DataFrame({'Chosen Facilities': facility_data})
network_df = pd.DataFrame(network_data, columns=['Echelon1 Cost', 'Echelon1 Time'])
# Save to Excel
with pd.ExcelWriter('results_MinCost.xlsx') as writer:
    results_df.to_excel(writer, sheet_name='Transportation Results', index=False)
    facility_df.to_excel(writer, sheet_name='Chosen Facilities', index=False)
    network_df.to_excel(writer, sheet_name='Network', index=False)


